In [54]:
%matplotlib qt
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Advection-Diffusion Animation', artist='Brian AC', comment='Advection-diffusion')
writer = FFMpegWriter(fps=20, metadata=metadata, bitrate = 100000)

# Initial conditions

In [41]:
circum = 40000 # meters, equator
time_length = 60 * 60 # 1 hour in seconds
plot_time = 5 * 60 # plot every third minute
lat_grid = 180 # Latitude grid
gauss_width = 20
velocity = 10 # m/s
diffusivity = 1000 # m^2/s
dx = circum / lat_grid # size of small steps in total circum
dt_velocity = dx / velocity
dt_diffusivity = dx**2 / diffusivity
dt = np.floor(min(dt_velocity,dt_diffusivity)) # choose the lesser time-step, which corresponds to the variable of interest
steps = int(time_length/dt)
steps_plot = 10 # plot every number of steps
dx_lon = 360/lat_grid
lon_grid = np.linspace(0,360-dx_lon,lat_grid)

### Store initial conditions in an easy to call array

In [43]:
class conditions:
    pass

init = conditions()
init.circum = circum
init.time_length = time_length
init.plot_time = plot_time
init.lat_grid = lat_grid
init.gauss_width = gauss_width
init.v = velocity
init.k = diffusivity
init.dx = dx
init.dt = dt
init.dx_lon = dx_lon
init.steps = steps
init.step = 0 # Where in the steps
init.steps_plot = steps_plot
init.utemp = np.zeros(lat_grid) # Plots
init.uplot1 = np.zeros(lat_grid)
init.scheme = 'Sample'
init.wave = 'InitialWave'

### Initial Functions

In [49]:
def singleWave(init):
    x = np.linspace(0, init.lat_grid - 1, num = init.lat_grid) * init.dx
    waveNumber = 5
    waveLength = init.circum/waveNumber
    gridWave = int(init.lat_grid/waveNumber)
    Amp = 1.
    u_0 = Amp * np.sin(x*np.pi/waveLength) # Wave, A * sin(x*pi/wavelength)
    
    return u_0

def gaussian(init):
    x = np.linspace(0, init.lat_grid - 1, num = init.lat_grid) * init.dx
    Amp = 1.      
    xmean = 0.5*np.mean(x)
    xstd = init.gauss_width/360*init.circum
    xstd2 = 2*(xstd**2)
    u_0 = Amp * np.exp (-(x-xmean)**2/xstd2) # Gaussian
        
    return u_0

def move(grid, shift): # Function that moves to the next grid element. If shift > 0, move forward. If < 0, move back
    shift = shift%len(grid)
    if shift>0:
        grid = np.concatenate([grid[shift:],grid[:shift]])  
    else:
        grid = np.concatenate([grid[:shift],grid[shift:]])  
    return grid

### Upstream function

In [45]:
def upstream(in_cond):
    mu = in_cond.v * in_cond.dt / in_cond.dx
    coeffk = in_cond.k * in_cond.dt / in_cond.dx**2
    
    uplot1 = in_cond.uplot1
    uplot1_jback = move(in_cond.uplot1,-1)
    uplot1_jforward = move(in_cond.uplot1,1)
    
    diffusion = coeffk * (uplot1_jback - 2*uplot1 + uplot1_jforward) # diffusion part of the equation

    in_cond.utemp = (1-mu)*uplot1 + mu*uplot1_jback + diffusion # advection + diffusion
    
    #save for the next time step
    in_cond.step = in_cond.step + 1   
    in_cond.uplot1 = in_cond.utemp
          
    return in_cond

### Plotting function

In [76]:
def plot_all(x, y, steps_plot, plottitle, label1):
    [N0,N1]=np.shape(y)    
    
    fig = plt.figure()
    with writer.saving(fig, "animation.mp4", dpi=200):
        for i in range(N0):        
            if i%steps_plot == 0:     #plot every steps_plot timestep
                plt.clf()
                ax=fig.subplots()
                 
                line1, = ax.plot(x, np.squeeze(y[i,:]), 'b', linewidth=2, label=label1)
                ax.set_ylim(-1,1)
                ax.legend(loc='lower right')
                ax.grid()
                plt.title(plottitle + '.   i=' + str(i))
                plt.show()
                plt.draw()
                plt.pause(0.05)
                writer.grab_frame()

### Function that runs a scheme (in this case, the Upstream scheme) and plots everything

In [80]:
def runscheme(init, InitialWave, Scheme, Label):
    u_0 = singleWave(init) # Initial condition (single wave)
    
    steps = init.steps
    lat_grid = init.lat_grid
    init.wave = InitialWave
    init.scheme = Scheme
    init.u_0 = u_0 # Initial condition
    init.utemp = u_0
    init.uplot1 = u_0
    init.step = 0
    init.umatrix = np.zeros((steps,lat_grid), dtype = float)
    
    # Integration
    
    count = init
    count.umatrix[0,:] = count.uplot1
    if Scheme == 'upstream':
        for i in range(steps):
            count = upstream(count)
            count.umatrix[i,:] = count.utemp
            
    # Plotting
    
    plottitle= init.scheme + ': ' + init.wave + ', velocity=%s, diffusivity=%s, dt=%.2f'%(init.v, init.k,init.dt)
    print(plottitle)
    
    lon = np.linspace(0,360-init.dx_lon,init.lat_grid)
    x = np.linspace(0., init.circum, init.lat_grid)
    
    plot_all(lon, count.umatrix, init.steps_plot,plottitle,Label) 
    
    return count.umatrix

## Plot: Single wave, Upstream scheme, no diffusion, velocity = 10 m/s

In [84]:
init.v = velocity
init.k = 1.e-6
init.steps_plot = 2
dt_velocity = 0.8*np.floor(init.dx/init.v)
dx_lonin=[2., 1.]
dt_in = [dt_velocity, dt_velocity/2.]

init.dx_lon = dx_lonin[0]
init.lat_grid = int(360/init.dx_lon)
init.dx = init.circum/init.lat_grid
init.dt = dt_in[0]
init.steps = int(time_length/init.dt)  # total no of timesteps

Uupstream = runscheme(init, 'singleWave', 'upstream', 'Advection')

upstream: singleWave, velocity=10, diffusivity=1e-06, dt=17.60


## Plot: Gaussian wave, Upstream scheme, no velocity, diffusion = 1000 m^2/s, gaussian

In [85]:
init.v = 0.
init.k = diffusivity
dt_diffusivity = 0.8*np.floor(int(0.5*init.dx**2/init.k))
dx_lonin=[2., 2.]
dt_in = [dt_diffusivity, 0.5*dt_diffusivity]

init.dx_lon = dx_lonin[0]
init.lat_grid = int(360/init.dx_lon)
init.dx = init.circum/init.lat_grid
init.dt = dt_in[0]
    
init.steps = int(time_length/init.dt)  # total no of timesteps

Uupstream = runscheme(init, 'gaussian', 'upstream', 'Diffusion')

upstream: gaussian, velocity=0.0, diffusivity=1000, dt=19.20


## Plot: Gaussian, Upstream scheme, velocity = 10 m/s, diffusion = 1000 m^2/s

In [86]:
init.v = velocity
init.k = diffusivity
dt_diffusivity = 0.5*init.dx**2/init.k
dt_velocity = init.dx/init.v
dt = 0.5*np.floor(min(dt_diffusivity, dt_velocity))
dx_lonin=[2., 2.]
dt_in = [dt, 0.5*dt]

init.dx_lon = dx_lonin[0]
init.lat_grid = int(360/init.dx_lon)
init.dx = init.circum/init.lat_grid
init.dt = dt_in[0]
    
init.steps = int(time_length/init.dt)  # total no of timesteps
    
Uupstream = runscheme(init, 'gaussian', 'upstream', 'Advection-Diffusion')

upstream: gaussian, velocity=10, diffusivity=1000, dt=11.00
